In [1]:
import argparse
import os, sys
import time
import copy
import math
import pickle
import statistics

import numpy as np
import pandas as pd
import open3d as o3d
import torchvision
import pytorch3d
from tqdm import tqdm
import matplotlib.pyplot as plt
import plotly.graph_objects as go

# Import pytorch dependencies
import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim
from torch.utils.data import DataLoader
from torch.nn.modules.utils import _single, _pair, _triple
from torchsummary import summary

from pytorch3d.loss import chamfer_distance

# Import toolkits
from utils.visualization_3D_objects import *
from utils.preprocessing import *
from utils.read_object import *
from utils.model_averaging import *
from utils.model_PCA import *
from utils.morphable_model import *
from utils.model_evaluation import *

from model.model import *

Jupyter environment detected. Enabling Open3D WebVisualizer.
[Open3D INFO] WebRTC GUI backend enabled.
[Open3D INFO] WebRTCWindowSystem: HTTP handshake server disabled.


In [2]:
DATA_PATH = "./data/processedShapeNet/car/"
TRAIN_BATCH_SIZE = 12
VAL_BATCH_SIZE = 10
INITIAL_LR = 1e-3
MOMENTUM = 0.9
EPOCHS = 200
DECAY_EPOCHS = 30
DECAY = 0.7
CHECKPOINT_FOLDER = "./saved_model"
MODEL_TYPE = "PointNetAE"

### Import Preprocessed ModelNet40 cars (Run shapenet_preprocessing.ipynb first to get these data)

In [3]:
#load all aligned cars
f1 = open(DATA_PATH+'train.txt','rb')
X_train = pickle.load(f1)
f2 = open(DATA_PATH+'test.txt','rb')
X_test = pickle.load(f2)

In [4]:
TRAIN_BATCH_SIZE = 12
VAL_BATCH_SIZE = 10

# construct dataloader
train_loader = DataLoader(
    X_train, 
    batch_size=TRAIN_BATCH_SIZE, 
    shuffle=True, 
    num_workers=4
)
val_loader = DataLoader(
    X_test, 
    batch_size=VAL_BATCH_SIZE, 
    shuffle=False, 
    num_workers=4
)

### Load saved model

In [6]:
device = 'cuda' if torch.cuda.is_available() else 'cpu'
if device =='cuda':
    print("Run on GPU...")
else:
    print("Run on CPU...")
    
model_test = PointNet_AE(3, 2048)
state_dict = torch.load(os.path.join(CHECKPOINT_FOLDER, MODEL_TYPE + '.pth')) # change the path to your own checkpoint file
model_test.cuda()
model_test.load_state_dict(state_dict['state_dict'])
model_test.eval()

print(state_dict['epoch'])

Run on GPU...
115


In [22]:
x = val_loader.__iter__().next() # hack to grab a batch

inputs = x.float().to(device)

outputs, global_feat = model_test(inputs)

X = inputs.cpu().detach().numpy()[6]
X_hat = outputs.cpu().detach().numpy()[6]

draw3DPoints(X, "Original Car")
draw3DPoints(X_hat, "Reconstructed Car")

In [26]:

# Create figure
def draw3DpointsSlider(model, features, lower_bound, higher_bound, step_size, mod_place, car_idx):
    """
    features : np.ndarray (3n features, number of total chosen eigenvalues)
    mod_weights : np.ndarray (number of total chosen eigenvalues, 1), while keeping the chosen eigenvalue unchanged,
                  the others set to 0.
    X_avg : np.ndarray (3, n) vertices of the mean shape
    """
    fig = go.Figure()
    # Add traces, one for each slider step

    for step in np.arange(lower_bound, higher_bound, step_size):
        new_features = torch.clone(features)
        new_features[:, mod_place] = new_features[:, mod_place] * step

        X = model.decoder(new_features).cpu().detach().numpy()[car_idx]

        fig.add_trace(
            go.Scatter3d(
                visible=False,
                name="𝜈 = " + str(step),
                x=X[0],
                y=X[1],
                z=X[2],
                mode='markers', marker=dict(
                    size=1,
                    color=X[2],  # set color to an array/list of desired values
                    colorscale='Viridis'
                )
            )

        )

    # Make 10th trace visible
    fig.data[0].visible = True

    # Create and add slider
    steps = []

    for i in range(len(fig.data)):
        step = dict(
            method="update",
            args=[{"visible": [False] * len(fig.data)},
                  {"title": "Feature No.%d" % (mod_place)}],  # layout attribute
        )
        step["args"][0]["visible"][i] = True  # Toggle i'th trace to "visible"
        steps.append(step)

    sliders = [dict(
        active=50,
        currentvalue={"prefix": "Frequency: "},
        pad={"t": 50},
        steps=steps
    )]
    
    x_range = np.max(X[0]) - np.min(X[0])
    y_range = np.max(X[1]) - np.min(X[1])
    z_range = np.max(X[2]) - np.min(X[2])
    max_range = max(x_range, max(y_range, z_range))

    fig.update_layout(
        scene = dict(
                    xaxis = dict(range=[np.min(X[0]) - x_range*0.1, np.max(X[0]) + x_range*0.1],),
                    yaxis = dict(range=[np.min(X[1]) - y_range*0.1, np.max(X[1]) + y_range*0.1],),
                    zaxis = dict(range=[np.min(X[2]) - z_range*0.1, np.max(X[2]) + z_range*0.1],),
                    aspectratio = dict(x=((np.max(X[0]) + x_range*0.1) - (np.min(X[0]) - x_range*0.1))/max_range,
                                       y=((np.max(X[1]) + y_range*0.1) - (np.min(X[1]) - y_range*0.1))/max_range,
                                       z=((np.max(X[2]) + z_range*0.1) - (np.min(X[2]) - z_range*0.1))/max_range)
                    ),
        width = 1000,
        height = 700,
        sliders=sliders
    )

    fig.show()



In [27]:
draw3DpointsSlider(model_test, global_feat, -10, 10, 1, 0, 6)